
## Overview

This notebook will show you how to create and query a table or DataFrame that you uploaded to DBFS. [DBFS](https://docs.databricks.com/user-guide/dbfs-databricks-file-system.html) is a Databricks File System that allows you to store data for querying inside of Databricks. This notebook assumes that you have a file already inside of DBFS that you would like to read from.

This notebook is written in **Python** so the default cell type is Python. However, you can use different languages by using the `%LANGUAGE` syntax. Python, Scala, SQL, and R are all supported.

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import when, col,length, expr
from pyspark.sql import functions as F

#load the csv into a data frame - bronze state 

# File location and type
file_location = "/FileStore/tables/rotten_tomatoes_top_movies.csv"
file_type = "csv"

# CSV options
infer_schema = "false"
first_row_is_header = "True"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df)

_c0 title year synopsis critic_score people_score consensus total_reviews total_ratings type rating genre original_language director producer writer release_date_(theaters) release_date_(streaming) box_office_(gross_usa) runtime production_co sound_mix aspect_ratio view_the_collection crew link 0 Black Panther 2018 After the death of his father, T'Challa returns home to the African nation of Wakanda to take his rightful place as king. When a powerful enemy suddenly reappears, T'Challa's mettle as king -- and as Black Panther -- gets tested when he's drawn into a conflict that puts the fate of Wakanda and the entire world at risk. Faced with treachery and danger, the young king must rally his allies and release the full power of Black Panther to defeat his foes and secure the safety of his people. 96 79 Black Panther elevates superhero cinema to thrilling new heights while telling one of the MCU's most absorbing stories -- and introducing some of its most fully realized characters. 519 50,000+ Action & Adventure PG-13 (Sequences of Action Violence|A Brief Rude Gesture) adventure, action, fantasy English Ryan Coogler Kevin Feige Ryan Coogler, Joe Robert Cole Feb 16, 2018 wide May 2, 2018 $700.2M 2h 14m Walt Disney Pictures DTS, Dolby Atmos Scope (2.35:1) Marvel Cinematic Universe Chadwick Boseman, Michael B. Jordan, Lupita Nyong'o, Danai Gurira, Martin Freeman, Daniel Kaluuya, Letitia Wright, Winston Duke, Angela Bassett, Forest Whitaker, Ryan Coogler, Ryan Coogler, Joe Robert Cole, Kevin Feige, Louis D'Esposito, Victoria Alonso, Nate Moore, Jeffrey Chernov, Stan Lee, Rachel Morrison http://www.rottentomatoes.com/m/black_panther_2018 1 Avengers: Endgame 2019 Adrift in space with no food or water, Tony Stark sends a message to Pepper Potts as his oxygen supply starts to dwindle. Meanwhile, the remaining Avengers -- Thor, Black Widow, Captain America and Bruce Banner -- must figure out a way to bring back their vanquished allies for an epic showdown with Thanos -- the evil demigod who decimated the planet and the universe. 94 90 Exciting, entertaining, and emotionally impactful, Avengers: Endgame does whatever it takes to deliver a satisfying finale to Marvel's epic Infinity Saga. 538 50,000+ Action & Adventure PG-13 (Sequences of Sci-Fi Violence|Action|Some Language) sci fi, adventure, action, fantasy English Anthony Russo, Joe Russo Kevin Feige Christopher Markus, Stephen McFeely Apr 26, 2019 wide Jul 30, 2019 $858.4M 3h 1m Marvel Studios, Walt Disney Pictures Dolby Atmos, DTS, Dolby Digital, SDDS Scope (2.35:1) Marvel Cinematic Universe Robert Downey Jr., Chris Evans, Mark Ruffalo, Chris Hemsworth, Scarlett Johansson, Jeremy Renner, Brie Larson, Paul Rudd, Don Cheadle, Karen Gillan, Anthony Russo, Joe Russo, Christopher Markus, Stephen McFeely, Kevin Feige, Louis D'Esposito, Victoria Alonso, Michael Grillo, Trinh Tran, Jon Favreau http://www.rottentomatoes.com/m/avengers_endgame 2 Mission: Impossible -- Fallout 2018 Ethan Hunt and the IMF team join forces with CIA assassin August Walker to prevent a disaster of epic proportions. Arms dealer John Lark and a group of terrorists known as the Apostles plan to use three plutonium cores for a simultaneous nuclear attack on the Vatican, Jerusalem and Mecca, Saudi Arabia. When the weapons go missing, Ethan and his crew find themselves in a desperate race against time to prevent them from falling into the wrong hands. 97 88 "Fast, sleek, and fun, Mission: Impossible - Fallout lives up to the ""impossible"" part of its name by setting yet another high mark for insane set pieces in a franchise full of them." 433 10,000+ Action & Adventure PG-13 (Intense Sequences of Action|Brief Strong Language|Violence) action, mystery and thriller, adventure English Christopher McQuarrie Tom Cruise, Christopher McQuarrie, Jake Myers, J.J. Abrams Christopher McQuarrie Jul 27, 2018 wide Nov 20, 2018 $220.1M 2h 27m Bad Robot, Tom Cruise DTS, Dolby Atmos, Dolby Digital Scope (2.35:1) null Tom Cruise, Henry 

In [0]:

#load the columns wanted for the results into a new data frame - start of silver stage 

df_select = df["year","critic_score","people_score","type","box_office_(gross_usa)"]


#some of the result sets have text in place of the integer columns critic score and people score this needs cleaning
#find and remove non integer values in the score columns 
df_clean = df_select.withColumn("critic_score", F.col("critic_score").cast("float")) \
                    .withColumn("people_score", F.col("people_score").cast("float"))
df_clean = df_clean.dropna(how='any')


#remove non category records from type field 

df_clean = df_clean.withColumn('type', when(col('type').rlike("^\d"),None).otherwise(col('type')))
df_clean = df_clean.dropna(how='any')


#Clean type field from symbols which start the field 

char_to_remove = ['>','<','^','&','$','£']

df_clean = df_clean.withColumn(
    'type', 
    F.when(
        F.col('type').isin(char_to_remove),col('type').substr(2,100)
        ).otherwise(col('type')
                    )
        )


#remove the $ and M from the box office column
df_clean = df_clean.withColumn(
    'box_office_(gross_usa)',
    F.when(
        F.col('box_office_(gross_usa)').rlike("^[\$\d]"), 
        F.regexp_replace(F.col('box_office_(gross_usa)'), '[$,M]', '')
    ).otherwise(F.col('box_office_(gross_usa)'))
)


#First result set is the difference between critic score and public score over the time frame 
df_clean = df_clean.withColumn('score_difference', F.col('critic_score') - F.col('people_score'))
year_difference = df_clean.groupby('year').agg(F.avg('score_difference').alias('avg_score_difference'))
year_difference = year_difference.orderBy('year',ascending=False)
year_difference.show()
#see which type has the highest box office - does not account for inflation 
type_amount = df_clean.groupby('type').agg(F.avg('box_office_(gross_usa)').alias('box_office_(gross_usa)'))
type_amount = type_amount.orderBy('box_office_(gross_usa)',ascending=False)
type_amount.show()

+----+--------------------+
|year|avg_score_difference|
+----+--------------------+
|2020|  15.846153846153847|
|2019|  11.043478260869565|
|2018|  13.623188405797102|
|2017|  10.586666666666666|
|2016|  12.133333333333333|
|2015|  11.241379310344827|
|2014|  10.280701754385966|
|2013|   13.27027027027027|
|2012|  11.621621621621621|
|2011|    9.76595744680851|
|2010|               8.225|
|2009|               11.75|
|2008|   7.181818181818182|
|2007|   8.454545454545455|
|2006| 0.47619047619047616|
|2005|                 1.9|
|2004|               7.375|
|2003|                 2.1|
|2002|  14.461538461538462|
|2001|  1.7894736842105263|
+----+--------------------+
only showing top 20 rows

+--------------------+----------------------+
|                type|box_office_(gross_usa)|
+--------------------+----------------------+
|  Action & Adventure|    224.03731343283573|
|Science Fiction &...|    204.47419354838706|
|       Kids & Family|     161.7131147540984|
|           Animation|    